<a href="https://colab.research.google.com/github/towardsai/ai-tutor-rag-system/blob/main/notebooks/15-Use_OpenSource_Models.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Packages and Setup Variables

In [ ]:
!pip install -q llama-index==0.10.11 openai==1.12.0 llama-index-finetuning llama-index-llms-together llama-index-llms-gemini llama-index-embeddings-huggingface llama-index-readers-web llama-index-vector-stores-chroma tiktoken==0.6.0 chromadb==0.4.22 pandas==2.2.0 html2text sentence_transformers pydantic kaleido==0.2.1

In [ ]:
import os

# Set environment variables for the API keys
os.environ["OPENAI_API_KEY"] = "<YOUR_API_KEY>"
os.environ["TOGETHER_AI_API_TOKEN"] = "<YOUR_API_KEY>"
os.environ["GOOGLE_API_KEY"] = "<YOUR_API_KEY>"

# Allows running asyncio in environments with an existing event loop, like Jupyter notebooks.
import nest_asyncio

nest_asyncio.apply()

# Create a vector store and ingest articles

In [ ]:
import chromadb
from llama_index.vector_stores.chroma import ChromaVectorStore

# create vector store
vector_store_name = "mini-llama-articles"
chroma_client = chromadb.PersistentClient(path=vector_store_name)
chroma_collection = chroma_client.get_or_create_collection(vector_store_name)
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)

The dataset includes several articles from the TowardsAI blog, which provide an in-depth explanation of the LLaMA2 model. Read the dataset as a long string.

In [ ]:
!curl -o ./mini-llama-articles.csv https://raw.githubusercontent.com/AlaFalaki/tutorial_notebooks/main/data/mini-llama-articles.csv

## Read articles from file

In [ ]:
import csv

rows = []

# Load the file as a JSON
with open("./mini-llama-articles.csv", mode="r", encoding="utf-8") as file:
  csv_reader = csv.reader(file)

  for idx, row in enumerate( csv_reader ):
    if idx == 0: continue; # Skip header row
    rows.append(row)

## Ingest documents into vector store

In [ ]:
from llama_index.core import Document
from llama_index.core.text_splitter import TokenTextSplitter
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core.ingestion import IngestionPipeline

# Convert the chunks to Document objects so the LlamaIndex framework can process them.
documents = [Document(text=row[1], metadata={"title": row[0], "url": row[2], "source_name": row[3]}) for row in rows]

# Define the splitter object that split the text into segments with 512 tokens,
# with a 128 overlap between the segments.
text_splitter = TokenTextSplitter(
    separator=" ", chunk_size=512, chunk_overlap=128
)

# Create the pipeline to apply the transformation on each chunk,
# and store the transformed text in the chroma vector store.
pipeline = IngestionPipeline(
    transformations=[
        text_splitter,
        HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5") # Or, OpenAIEmbedding()
    ],
    vector_store=vector_store
)

nodes = pipeline.run(documents=documents, show_progress=True)

# Load vector store and create query engine

In [ ]:
from llama_index.core import ServiceContext
from llama_index.core import VectorStoreIndex

def from_vector_store_to_index(vector_store, llm, embed_model):
    # Define a ServiceContext that uses the BGE model for embedding which will be loaded from Huggingface.
    # The model will be downloaded to your local machine.
    service_context = ServiceContext.from_defaults(llm=llm, embed_model=embed_model)

    # Create the index based on the vector store.
    index = VectorStoreIndex.from_vector_store(vector_store, service_context=service_context)

    return index

In [ ]:
from llama_index.core.prompts import PromptTemplate
from llama_index.llms.together import TogetherLLM

# Use the Together AI service to access the LLaMA2-70B chat model
llm = TogetherLLM(
    model="meta-llama/Meta-Llama-3.1-70B-Instruct-Turbo",
    api_key=os.environ["TOGETHER_AI_API_TOKEN"]
)

# create index from vector store
index = from_vector_store_to_index(vector_store, llm, "local:BAAI/bge-small-en-v1.5")

# Define a query engine that is responsible for retrieving related pieces of text,
# and using a LLM to formulate the final answer.
query_engine = index.as_query_engine()

# Test query engine

In [ ]:
res = query_engine.query("How many parameters LLaMA2 has?")
print(res.response)
# 'Llama 2 is available in four different model sizes: 7 billion, 13 billion, 34 billion, and 70 billion parameters.'

In [ ]:
# print the source nodes used to write the answer
for src in res.source_nodes:
  print("Node ID\t", src.node_id)
  print("Title\t", src.metadata['title'])
  print("Text\t", src.text)
  print("Score\t", src.score)
  print("-_"*20)

# Evaluate the retriever

In [ ]:
from llama_index.core.evaluation import generate_question_context_pairs
from llama_index.llms.openai import OpenAI

# Create questions for each segment. These questions will be used to
# assess whether the retriever can accurately identify and return the
# corresponding segment when queried.
llm = OpenAI(model="gpt-3.5-turbo")
rag_eval_dataset = generate_question_context_pairs(
    nodes,
    llm=llm,
    num_questions_per_chunk=1
)

# We can save the evaluation dataset as a json file for later use.
rag_eval_dataset.save_json("./rag_eval_dataset.json")

If you have uploaded the generated question JSON file, please uncomment the code in the next cell block. This will avoid the need to generate the questions manually, saving you time and effort.

In [ ]:
from llama_index.finetuning.embeddings.common import (
    EmbeddingQAFinetuneDataset,
)
rag_eval_dataset = EmbeddingQAFinetuneDataset.from_json(
    "./rag_eval_dataset.json"
)

In [ ]:
from llama_index.core.evaluation import RetrieverEvaluator, RelevancyEvaluator, FaithfulnessEvaluator, BatchEvalRunner
from llama_index.llms.openai import OpenAI

async def run_evaluation(index, rag_eval_dataset, top_k_values, llm_judge, n_queries_to_evaluate=20):
    evaluation_results = {}

    # ------------------- MRR and Hit Rate -------------------

    for top_k in top_k_values:
        # Get MRR and Hit Rate
        retriever = index.as_retriever(similarity_top_k=top_k)
        retriever_evaluator = RetrieverEvaluator.from_metric_names(
            ["mrr", "hit_rate"], retriever=retriever
        )
        eval_results = await retriever_evaluator.aevaluate_dataset(rag_eval_dataset)
        avg_mrr = sum(res.metric_vals_dict["mrr"] for res in eval_results) / len(eval_results)
        avg_hit_rate = sum(res.metric_vals_dict["hit_rate"] for res in eval_results) / len(eval_results)

        # Collect the evaluation results
        evaluation_results[f"mrr_@_{top_k}"] = avg_mrr
        evaluation_results[f"hit_rate_@_{top_k}"] = avg_hit_rate

    # ------------------- Faithfulness and Relevancy -------------------

    # Extract the questions from the dataset
    queries = list(rag_eval_dataset.queries.values())
    batch_eval_queries = queries[:n_queries_to_evaluate]

    # Initiate the faithfulnes and relevancy evaluator objects
    faithfulness_evaluator = FaithfulnessEvaluator(llm=llm_judge)
    relevancy_evaluator = RelevancyEvaluator(llm=llm_judge)

    # The batch evaluator runs the evaluation in batches
    runner = BatchEvalRunner(
        {
            "faithfulness": faithfulness_evaluator,
            "relevancy": relevancy_evaluator
        },
        workers=16,
    )

    # Get faithfulness and relevancy scores
    query_engine = index.as_query_engine()
    eval_results = await runner.aevaluate_queries(
        query_engine, queries=batch_eval_queries
    )
    faithfulness_score = sum(result.passing for result in eval_results['faithfulness']) / len(eval_results['faithfulness'])
    relevancy_score = sum(result.passing for result in eval_results['relevancy']) / len(eval_results['relevancy'])
    evaluation_results["faithfulness"] = faithfulness_score
    evaluation_results["relevancy"] = relevancy_score

    return evaluation_results

In [ ]:
# We evaluate the retrievers with different top_k values.
top_k_values = [2, 4, 6, 8, 10]
llm_judge = OpenAI(temperature=0, model="gpt-4o")
evaluation_results = await run_evaluation(index, rag_eval_dataset, top_k_values, llm_judge, n_queries_to_evaluate=20)

In [ ]:
print(evaluation_results)

In [ ]:
# Use GPT-3.5-turbo as the LLM model
llm = OpenAI(model="gpt-3.5-turbo")

# create index from vector store
index = from_vector_store_to_index(vector_store, llm, "local:BAAI/bge-small-en-v1.5")

# run evaluation with GPT-3.5-turbo
top_k_values = [2, 4, 6, 8, 10]
llm_judge = OpenAI(temperature=0, model="gpt-4o")
evaluation_results = await run_evaluation(index, rag_eval_dataset, top_k_values, llm_judge, n_queries_to_evaluate=20)

In [ ]:
print(evaluation_results)

In [ ]:
from llama_index.llms.gemini import Gemini

# Use Gemini as the LLM model
llm = Gemini(model="models/gemini-1.5-flash")

# create index from vector store
index = from_vector_store_to_index(vector_store, llm, "local:BAAI/bge-small-en-v1.5")

# run evaluation with Gemini
top_k_values = [2, 4, 6, 8, 10]
llm_judge = OpenAI(temperature=0, model="gpt-4o")
evaluation_results = await run_evaluation(index, rag_eval_dataset, top_k_values, llm_judge, n_queries_to_evaluate=20)

In [ ]:
print(evaluation_results)

# Inference speed comparison

In [ ]:
import time

In [ ]:
llm = TogetherLLM(
    model="meta-llama/Meta-Llama-3.1-70B-Instruct-Turbo",
    api_key=os.environ["TOGETHER_AI_API_TOKEN"]
)

time_start = time.time()
llm.complete("List the 50 states in the United States of America. Write their names in a comma-separated list and nothing else.")
time_end = time.time()
print("Time taken for Llama 3.1 70B on Together AI: {0:.2f} seconds".format(time_end - time_start))

In [ ]:
llm = OpenAI(model="gpt-3.5-turbo")

time_start = time.time()
llm.complete("List the 50 states in the United States of America. Write their names in a comma-separated list and nothing else.")
time_end = time.time()
print("Time taken for GPT 3.5 Turbo: {0:.2f} seconds".format(time_end - time_start))

In [ ]:
llm = Gemini(model="models/gemini-1.5-flash")

time_start = time.time()
llm.complete("List the 50 states in the United States of America. Write their names in a comma-separated list and nothing else.")
time_end = time.time()
print("Time taken for Gemini 1.5 Flash: {0:.2f} seconds".format(time_end - time_start))